In [34]:
import os
import time
import json
import pandas as pd
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.chrome.options import Options
from selenium.common.exceptions import TimeoutException, NoSuchElementException
from google.oauth2 import service_account
from googleapiclient.discovery import build
from google.oauth2.service_account import Credentials
from googleapiclient import discovery
from googleapiclient.errors import HttpError

In [18]:
def save_data_to_excel(data, file_name):
    df = pd.DataFrame(data)
    if os.path.exists(file_name):
        existing_data = pd.read_excel(file_name)
        combined_data = pd.concat([existing_data, df], ignore_index=True)
        combined_data.to_excel(file_name, index=False)
    else:
        df.to_excel(file_name, index=False)


In [2]:
user_agent = "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/112.0.0.0 Safari/537.36"

In [3]:
url = "https://www.bigbasket.com/"

In [4]:
chrome_options = webdriver.ChromeOptions()
chrome_options.add_argument("--incognito")
chrome_options.add_argument(f'user_agent={user_agent}')
chrome_options.add_argument("--disable-blink-features=AutomationControlled")
chrome_options.add_argument("--disable-infobars")
chrome_options.add_argument("--headless")
driver = webdriver.Chrome(options=chrome_options)
driver.get(url)
wait = WebDriverWait(driver, 10)

In [5]:
ul_element = wait.until(EC.presence_of_element_located((By.ID, 'navBarMegaNav')))
li_elements = ul_element.find_elements(By.CSS_SELECTOR, 'li')[:7]

cat_urls = []
for li_element in li_elements:
    a_element = li_element.find_element(By.CSS_SELECTOR, 'a.ng-binding')
    href_link = a_element.get_attribute('href')
    cat_urls.append(href_link)
cat_urls = cat_urls[1:6]

cat_urls

['https://www.bigbasket.com/cl/foodgrains-oil-masala/?nc=nb',
 'https://www.bigbasket.com/cl/bakery-cakes-dairy/?nc=nb',
 'https://www.bigbasket.com/cl/beverages/?nc=nb',
 'https://www.bigbasket.com/cl/snacks-branded-foods/?nc=nb',
 'https://www.bigbasket.com/cl/beauty-hygiene/?nc=nb']

In [10]:
for cat_url in cat_urls:
    driver.get(cat_url)

    wait = WebDriverWait(driver, 20)

    try:
        div_elements = wait.until(EC.presence_of_all_elements_located((By.CSS_SELECTOR, 'div.col-xs-12.checkbox.subcat.ng-scope')))

        # Extract the href links from the <a> tags within the <div> elements
        subcat_urls = []
        for div_element in div_elements:
            a_element = div_element.find_element(By.CSS_SELECTOR, 'a')
            href_link = a_element.get_attribute('href')
            subcat_urls.append(href_link)

        print(f'Category URL: {cat_url}')
        print('Subcategory URLs:', subcat_urls)

    except TimeoutException:
        print(f"Unable to find subcategories for {cat_url}, skipping to the next link.")

Category URL: https://www.bigbasket.com/cl/foodgrains-oil-masala/?nc=nb
Subcategory URLs: ['https://www.bigbasket.com/pc/foodgrains-oil-masala/atta-flours-sooji/?nc=ct-fa&sid=ldF2No-ibWQBoWMBqHNrdV9saXN0kKJuZsOiY2OjMzgxqWJhdGNoX2lkeACiYW_ConVywqJhcMOibHTNAS2jZHNqzSa0oW-qcG9wdWxhcml0eaVzcl9pZAGiZHPNBrijbXJpAQ==', 'https://www.bigbasket.com/pc/foodgrains-oil-masala/dals-pulses/?nc=ct-fa&sid=ldF2No-ibWQBoWMBqHNrdV9saXN0kKJuZsOiY2OjMzgxqWJhdGNoX2lkeACiYW_ConVywqJhcMOibHTNAS2jZHNqzSa0oW-qcG9wdWxhcml0eaVzcl9pZAGiZHPNBrijbXJpAQ==', 'https://www.bigbasket.com/pc/foodgrains-oil-masala/dry-fruits/?nc=ct-fa&sid=ldF2No-ibWQBoWMBqHNrdV9saXN0kKJuZsOiY2OjMzgxqWJhdGNoX2lkeACiYW_ConVywqJhcMOibHTNAS2jZHNqzSa0oW-qcG9wdWxhcml0eaVzcl9pZAGiZHPNBrijbXJpAQ==', 'https://www.bigbasket.com/pc/foodgrains-oil-masala/edible-oils-ghee/?nc=ct-fa&sid=ldF2No-ibWQBoWMBqHNrdV9saXN0kKJuZsOiY2OjMzgxqWJhdGNoX2lkeACiYW_ConVywqJhcMOibHTNAS2jZHNqzSa0oW-qcG9wdWxhcml0eaVzcl9pZAGiZHPNBrijbXJpAQ==', 'https://www.bigbasket.com/pc/f

In [11]:

all_product_links = []  # This list will store all the product links

for cat_url in cat_urls:
    driver.get(cat_url)
    wait = WebDriverWait(driver, 20)

    try:
        div_elements = wait.until(EC.presence_of_all_elements_located((By.CSS_SELECTOR, 'div.col-xs-12.checkbox.subcat.ng-scope')))

        subcat_urls = []
        for div_element in div_elements:
            a_element = div_element.find_element(By.CSS_SELECTOR, 'a')
            href_link = a_element.get_attribute('href')
            subcat_urls.append(href_link)
        
        for subcat_url in subcat_urls:
            driver.get(subcat_url)
            wait = WebDriverWait(driver, 20)

            try:
                product_divs = wait.until(EC.presence_of_all_elements_located((By.CSS_SELECTOR, 'div.col-xs-12.checkbox.subcat2.ng-scope')))

                for product_div in product_divs:
                    try:
                        product_a = product_div.find_element(By.CSS_SELECTOR, 'a')
                        product_href = product_a.get_attribute('href')
                        all_product_links.append(product_href)
                    except NoSuchElementException:
                        print("Unable to find <a> tag inside the product div. Skipping this product.")

            except TimeoutException:
                print(f"Unable to find product links for {subcat_url}, skipping to the next link.")

    except TimeoutException:
        print(f"Unable to find subcategories for {cat_url}, skipping to the next link.")

print("All Product Links:", all_product_links)


All Product Links: ['https://www.bigbasket.com/pc/foodgrains-oil-masala/atta-flours-sooji/atta-whole-wheat/?nc=ct-fa&sid=a4vuS4-ibWQBoWMBqHNrdV9saXN0kKJuZsOiY2OoMzgxfDE0NDepYmF0Y2hfaWR4AKJhb8KidXLComFww6JsdM0BLaNkc2rNJrShb6pwb3B1bGFyaXR5pXNyX2lkAaJkc80GuKNtcmkB', 'https://www.bigbasket.com/pc/foodgrains-oil-masala/atta-flours-sooji/rice-other-flours/?nc=ct-fa&sid=a4vuS4-ibWQBoWMBqHNrdV9saXN0kKJuZsOiY2OoMzgxfDE0NDepYmF0Y2hfaWR4AKJhb8KidXLComFww6JsdM0BLaNkc2rNJrShb6pwb3B1bGFyaXR5pXNyX2lkAaJkc80GuKNtcmkB', 'https://www.bigbasket.com/pc/foodgrains-oil-masala/atta-flours-sooji/sooji-maida-besan/?nc=ct-fa&sid=a4vuS4-ibWQBoWMBqHNrdV9saXN0kKJuZsOiY2OoMzgxfDE0NDepYmF0Y2hfaWR4AKJhb8KidXLComFww6JsdM0BLaNkc2rNJrShb6pwb3B1bGFyaXR5pXNyX2lkAaJkc80GuKNtcmkB', 'https://www.bigbasket.com/pc/foodgrains-oil-masala/atta-flours-sooji/atta-whole-wheat/?nc=ct-fa&sid=a4vuS4-ibWQBoWMBqHNrdV9saXN0kKJuZsOiY2OoMzgxfDE0NDepYmF0Y2hfaWR4AKJhb8KidXLComFww6JsdM0BLaNkc2rNJrShb6pwb3B1bGFyaXR5pXNyX2lkAaJkc80GuKNtcmkB', 'h

In [8]:
all_product_links

['https://www.bigbasket.com/pc/foodgrains-oil-masala/atta-flours-sooji/atta-whole-wheat/?nc=ct-fa&sid=a4vuS4-ibWQBoWMBqHNrdV9saXN0kKJuZsOiY2OoMzgxfDE0NDepYmF0Y2hfaWR4AKJhb8KidXLComFww6JsdM0BLaNkc2rNJrShb6pwb3B1bGFyaXR5pXNyX2lkAaJkc80GuKNtcmkB',
 'https://www.bigbasket.com/pc/foodgrains-oil-masala/atta-flours-sooji/rice-other-flours/?nc=ct-fa&sid=a4vuS4-ibWQBoWMBqHNrdV9saXN0kKJuZsOiY2OoMzgxfDE0NDepYmF0Y2hfaWR4AKJhb8KidXLComFww6JsdM0BLaNkc2rNJrShb6pwb3B1bGFyaXR5pXNyX2lkAaJkc80GuKNtcmkB',
 'https://www.bigbasket.com/pc/foodgrains-oil-masala/atta-flours-sooji/sooji-maida-besan/?nc=ct-fa&sid=a4vuS4-ibWQBoWMBqHNrdV9saXN0kKJuZsOiY2OoMzgxfDE0NDepYmF0Y2hfaWR4AKJhb8KidXLComFww6JsdM0BLaNkc2rNJrShb6pwb3B1bGFyaXR5pXNyX2lkAaJkc80GuKNtcmkB',
 'https://www.bigbasket.com/pc/foodgrains-oil-masala/atta-flours-sooji/atta-whole-wheat/?nc=ct-fa&sid=a4vuS4-ibWQBoWMBqHNrdV9saXN0kKJuZsOiY2OoMzgxfDE0NDepYmF0Y2hfaWR4AKJhb8KidXLComFww6JsdM0BLaNkc2rNJrShb6pwb3B1bGFyaXR5pXNyX2lkAaJkc80GuKNtcmkB',
 'https://www.bigb

In [12]:
item_links = []  # This list will store the href links of 10 items from each product link

for product_link in all_product_links:
    driver.get(product_link)
    wait = WebDriverWait(driver, 20)

    try:
        item_divs = wait.until(EC.presence_of_all_elements_located((By.CSS_SELECTOR, 'div.col-sm-12.col-xs-5.prod-view.ng-scope')))

        # Get the first 10 href links
        for item_div in item_divs[:10]:
            try:
                item_a = item_div.find_element(By.CSS_SELECTOR, 'a')
                item_href = item_a.get_attribute('href')
                item_links.append(item_href)
            except NoSuchElementException:
                print("Unable to find <a> tag inside the item div. Skipping this item.")

    except TimeoutException:
        print(f"Unable to find items for {product_link}, skipping to the next link.")

item_links

['https://www.bigbasket.com/pd/126906/aashirvaad-atta-whole-wheat-10-kg-pouch/?nc=l3category&t_pg=L3Categories&t_p=l3category&t_s=l3category&t_pos=3&t_ch=desktop',
 'https://www.bigbasket.com/pd/1220743/aashirvaad-atta-whole-wheat-5-kg-iodised-salt-1-kg-combo-pouch/?nc=l3category&t_pg=L3Categories&t_p=l3category&t_s=l3category&t_pos=3&t_ch=desktop',
 'https://www.bigbasket.com/pd/1220742/aashirvaad-atta-whole-wheat-10-kg-iodised-salt-1-kg-combo-pouch/?nc=l3category&t_pg=L3Categories&t_p=l3category&t_s=l3category&t_pos=3&t_ch=desktop',
 'https://www.bigbasket.com/pd/40236231/aashirvaad-select-sharbati-atta-100-mp-whole-wheat-rotis-stay-softer-for-longer-10-kg/?nc=l3category&t_pg=L3Categories&t_p=l3category&t_s=l3category&t_pos=3&t_ch=desktop',
 'https://www.bigbasket.com/pd/40236230/aashirvaad-atta-with-multigrains-high-fibre-soft-rotis-10-kg/?nc=l3category&t_pg=L3Categories&t_p=l3category&t_s=l3category&t_pos=3&t_ch=desktop',
 'https://www.bigbasket.com/pd/40189429/bb-royal-superior-mp

In [19]:
all_data = []

time_interval = 1 * 60  # 1 minutes in seconds
start_time = time.time()
excel_file = "bigbasket_data.xlsx"

for item_link in item_links:

    try:
        driver.get(item_link)

        # 1. Get the City
        city = ""
        print("City:", city)

        # 2. Get Category, Sub-Category, and Product
        div_category = driver.find_element(By.CSS_SELECTOR, "div._3moNK")
        a_tags = div_category.find_elements(By.CSS_SELECTOR, "a._3WUR_._3bj9B.rippleEffect")[1:]
        category, sub_category, product = [a_tag.text.replace(">", "").strip() for a_tag in a_tags]
        print("Category:", category)
        print("Sub-Category:", sub_category)
        print("Product:", product)

        # 3. Get SKU ID
        sku_id = item_link.split("/")[-3]
        print("SKU ID:", sku_id)

        # 4. Get Image
        image_div = driver.find_element(By.CSS_SELECTOR, "div._2FbOx")
        image = image_div.find_element(By.CSS_SELECTOR, "img._3oKVV").get_attribute("src")
        print("Image:", image)

        # 5. Get Brand
        brand_div = driver.find_element(By.CSS_SELECTOR, "div._2yfKw")
        brand = brand_div.find_element(By.CSS_SELECTOR, "a._2zLWN._3bj9B.rippleEffect").text
        print("Brand:", brand)

        # 6. Get SKU Name and SKU Size
        sku_div = driver.find_element(By.CSS_SELECTOR, "div._2yfKw")
        sku_string = sku_div.find_element(By.CSS_SELECTOR, "h1.GrE04").text
        sku_name = sku_string.split(" - ")[0].strip()
        sku_size = sku_string.split(",")[-1].strip()
        print("SKU Name:", sku_name)
        print("SKU Size:", sku_size)

        # 7. Get MRP and Selling Price
        price_div = driver.find_element(By.CSS_SELECTOR, "div#price")
        mrp_element = price_div.find_element(By.CSS_SELECTOR, "td._2ifWF")
        selling_price_element = price_div.find_element(By.CSS_SELECTOR, "td.IyLvo")
        mrp = mrp_element.text
        selling_price = selling_price_element.text

        print("MRP:", mrp)
        print("Selling Price:", selling_price)

        # 8. Get Item Link
        print("Item Link:", item_link)

        try:
            driver.find_element(By.CSS_SELECTOR, "div._36qqs")
            in_stock = "No"
        except NoSuchElementException:
            in_stock = "Yes"
        print("In Stock:", in_stock)

        # 9. Print Out of Stock
        out_of_stock = "Yes" if in_stock == "No" else "No"
        print("Out of Stock:", out_of_stock)
    
        data = {
            "City": city,
            "Category": category,
            "Sub-Category": sub_category,
            "Product": product,
            "SKU ID": sku_id,
            "Image": image,
            "Brand": brand,
            "SKU Name": sku_name,
            "SKU Size": sku_size,
            "MRP": mrp,
            "Selling Price": selling_price,
            "Item Link": item_link,
            "In Stock": in_stock,
            "Out of Stock": out_of_stock
        }
        all_data.append(data)

        current_time = time.time()
        if current_time - start_time >= time_interval:
            save_data_to_excel(all_data, excel_file)
            start_time = time.time()
            all_data = []
        
    except NoSuchElementException:
        print(f"Skipping item: {item_link}")
        continue

if all_data:
    save_data_to_excel(all_data, excel_file)


City: 
Category: FOODGRAINS, OIL & MASALA
Sub-Category: ATTA, FLOURS & SOOJI
Product: ATTA WHOLE WHEAT
SKU ID: 126906
Image: https://www.bigbasket.com/media/uploads/p/l/126906_8-aashirvaad-atta-whole-wheat.jpg
Brand: Aashirvaad
SKU Name: Aashirvaad Atta/Godihittu
SKU Size: 10 kg
MRP: Rs 576
Selling Price: Rs 480
Item Link: https://www.bigbasket.com/pd/126906/aashirvaad-atta-whole-wheat-10-kg-pouch/?nc=l3category&t_pg=L3Categories&t_p=l3category&t_s=l3category&t_pos=3&t_ch=desktop
In Stock: Yes
Out of Stock: No
City: 
Category: FOODGRAINS, OIL & MASALA
Sub-Category: ATTA, FLOURS & SOOJI
Product: ATTA WHOLE WHEAT
SKU ID: 1220743
Image: https://www.bigbasket.com/media/uploads/p/l/1220743_1-aashirvaad-atta-whole-wheat-5-kg-iodised-salt-1-kg.jpg
Brand: Aashirvaad
SKU Name: Aashirvaad Atta
SKU Size: Combo 2 Items
MRP: Rs 346
Selling Price: Rs 324.80
Item Link: https://www.bigbasket.com/pd/1220743/aashirvaad-atta-whole-wheat-5-kg-iodised-salt-1-kg-combo-pouch/?nc=l3category&t_pg=L3Categories&

In [35]:
SCOPES = ['https://www.googleapis.com/auth/spreadsheets', 'https://www.googleapis.com/auth/drive']

def excel_to_google_sheets(excel_file, spreadsheet_name, sheet_name, credentials_json, my_email):
    try:
        credentials = Credentials.from_service_account_info(credentials_json).with_scopes(SCOPES)
        service = discovery.build('sheets', 'v4', credentials=credentials)

        # Create a new Google Sheets file
        spreadsheet = service.spreadsheets().create(body={
            'properties': {
                'title': spreadsheet_name
            }
        }).execute()

        spreadsheet_id = spreadsheet.get('spreadsheetId')

        drive_service = discovery.build('drive', 'v3', credentials=credentials)
        permission = {
            'type': 'user',
            'role': 'writer',  # or 'owner' if you want full control
            'emailAddress': my_email
        }
        drive_service.permissions().create(
            fileId=spreadsheet_id,
            body=permission,
            fields='id'
        ).execute()

        df = pd.read_excel(excel_file)
        df.fillna("", inplace=True)  # Replace NaN values with empty strings
        sheet_data = [df.columns.tolist()] + df.values.tolist()
        body = {
            'values': sheet_data
        }

        service.spreadsheets().values().update(
            spreadsheetId=spreadsheet_id,
            range=sheet_name + '!A1',
            valueInputOption='RAW',
            body=body
        ).execute()

        print(f'Successfully uploaded the data to Google Sheets: {spreadsheet_name}')
        
        sheet_url = f"https://docs.google.com/spreadsheets/d/{spreadsheet_id}/edit"
        return sheet_url
    except HttpError as error:
        print(f"An error occurred: {error}")
        print(error.content)

In [36]:
with open("credentials.json") as file:
    credentials_json = json.load(file)

excel_file = "bigbasket_data.xlsx"
spreadsheet_name = "BigBasket Data"
sheet_name = "Sheet1"

my_email = "gujratigaurang@gmail.com"
sheet_url = excel_to_google_sheets(excel_file, spreadsheet_name, sheet_name, credentials_json, my_email)
print(f"The Google Sheet URL is: {sheet_url}")




Successfully uploaded the data to Google Sheets: BigBasket Data
The Google Sheet URL is: https://docs.google.com/spreadsheets/d/1yHnrsZoYC8QicN_yTg88oEH_UYPdos-24DJBWuz7ZRw/edit
